In [2]:
pip  install tensorflow

Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\python39\python.exe -m pip install --upgrade pip' command.


In [3]:
# Importing the requried libraries
import pandas as pd
import numpy as np
import torch
from math import ceil
from time import time
import tensorflow as tf

In [4]:
df = pd.read_csv ('data.csv', encoding= 'unicode_escape')
print(df)

       InvoiceNo StockCode                          Description  Quantity  \
0         536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1         536365     71053                  WHITE METAL LANTERN         6   
2         536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3         536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4         536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   
...          ...       ...                                  ...       ...   
541904    581587     22613          PACK OF 20 SPACEBOY NAPKINS        12   
541905    581587     22899         CHILDREN'S APRON DOLLY GIRL          6   
541906    581587     23254        CHILDRENS CUTLERY DOLLY GIRL          4   
541907    581587     23255      CHILDRENS CUTLERY CIRCUS PARADE         4   
541908    581587     22138        BAKING SET 9 PIECE RETROSPOT          3   

            InvoiceDate  UnitPrice  CustomerID         Country  
0        1

In [5]:
item_lookup = df[['StockCode', 'Description', 'UnitPrice']].drop_duplicates() # Only get unique item/description pairs
item_lookup['StockCode'] = df.StockCode.astype(str) # Encode as strings for future lookup ease
item_lookup['UnitPrice'] = df.UnitPrice.astype(float)

In [6]:
item_lookup

StockCode                          Description  UnitPrice
0         85123A   WHITE HANGING HEART T-LIGHT HOLDER       2.55
1          71053                  WHITE METAL LANTERN       3.39
2         84406B       CREAM CUPID HEARTS COAT HANGER       2.75
3         84029G  KNITTED UNION FLAG HOT WATER BOTTLE       3.39
4         84029E       RED WOOLLY HOTTIE WHITE HEART.       3.39
...          ...                                  ...        ...
540908       DOT                       DOTCOM POSTAGE     933.17
541297     22738            RIBBON REEL SNOWY VILLAGE       7.50
541540       DOT                       DOTCOM POSTAGE    1714.17
541541         M                               Manual     224.69
541633     20936                 FORKED CACTUS CANDLE       1.25

[18053 rows x 3 columns]

In [7]:
print(len(pd.unique(item_lookup['StockCode'])))
number_of_unique_items = pd.unique(item_lookup['StockCode'])

4070


In [8]:

map_stock_values = {}
stock_id = 1; 
for rows in item_lookup.itertuples():
    string = getattr(rows, "StockCode")
    if not(string  in map_stock_values.keys()):
        map_stock_values[string] = stock_id;
        stock_id += 1; 
map_stock_values

{'85123A': 1,
 '71053': 2,
 '84406B': 3,
 '84029G': 4,
 '84029E': 5,
 '22752': 6,
 '21730': 7,
 '22633': 8,
 '22632': 9,
 '84879': 10,
 '22745': 11,
 '22748': 12,
 '22749': 13,
 '22310': 14,
 '84969': 15,
 '22623': 16,
 '22622': 17,
 '21754': 18,
 '21755': 19,
 '21777': 20,
 '48187': 21,
 '22960': 22,
 '22913': 23,
 '22912': 24,
 '22914': 25,
 '21756': 26,
 '22728': 27,
 '22727': 28,
 '22726': 29,
 '21724': 30,
 '21883': 31,
 '10002': 32,
 '21791': 33,
 '21035': 34,
 '22326': 35,
 '22629': 36,
 '22659': 37,
 '22631': 38,
 '22661': 39,
 '21731': 40,
 '22900': 41,
 '21913': 42,
 '22540': 43,
 '22544': 44,
 '22492': 45,
 'POST': 46,
 '22086': 47,
 '20679': 48,
 '37370': 49,
 '21871': 50,
 '21071': 51,
 '21068': 52,
 '82483': 53,
 '82486': 54,
 '82482': 55,
 '82494L': 56,
 '21258': 57,
 '22114': 58,
 '21733': 59,
 '22386': 60,
 '85099C': 61,
 '21033': 62,
 '20723': 63,
 '84997B': 64,
 '84997C': 65,
 '21094': 66,
 '20725': 67,
 '21559': 68,
 '22352': 69,
 '21212': 70,
 '21975': 71,
 '21977'

In [9]:
item_user_history_ = df[["StockCode", "CustomerID"]]
# print(item_user_history.head())
item_user_history_["StockCodeID"] =  item_user_history_["StockCode"].map(lambda x: map_stock_values[x])
# print(item_user_history)
print(item_user_history_.head())
dictionary_users = {}


for  rows in item_user_history_.itertuples():
    dictionary_users[getattr(rows, "StockCode")] = []
for  rows in item_user_history_.itertuples():
    dictionary_users[getattr(rows, "StockCode")].append(getattr(rows, "CustomerID"))
print(len(dictionary_users))
dictionary_users


<ipython-input-9-4716af02ec64>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  item_user_history_["StockCodeID"] =  item_user_history_["StockCode"].map(lambda x: map_stock_values[x])


  StockCode  CustomerID  StockCodeID
0    85123A     17850.0            1
1     71053     17850.0            2
2    84406B     17850.0            3
3    84029G     17850.0            4
4    84029E     17850.0            5
4070


{'85123A': [17850.0,
  17850.0,
  17850.0,
  17511.0,
  13408.0,
  17850.0,
  15862.0,
  17850.0,
  16552.0,
  14729.0,
  16456.0,
  nan,
  13777.0,
  13777.0,
  13065.0,
  nan,
  15235.0,
  17850.0,
  17850.0,
  17732.0,
  17850.0,
  17850.0,
  17850.0,
  17850.0,
  17850.0,
  17850.0,
  17976.0,
  17850.0,
  17850.0,
  17685.0,
  17850.0,
  17850.0,
  15640.0,
  13798.0,
  18239.0,
  14395.0,
  16883.0,
  12841.0,
  17967.0,
  nan,
  14723.0,
  17198.0,
  14396.0,
  18055.0,
  18109.0,
  15708.0,
  15708.0,
  16931.0,
  16931.0,
  16814.0,
  18118.0,
  13831.0,
  17211.0,
  15880.0,
  15953.0,
  13174.0,
  nan,
  18219.0,
  nan,
  14748.0,
  15860.0,
  14344.0,
  16719.0,
  17682.0,
  13089.0,
  15356.0,
  17191.0,
  13495.0,
  15602.0,
  nan,
  18055.0,
  17511.0,
  17616.0,
  14733.0,
  14176.0,
  17511.0,
  13488.0,
  16221.0,
  15002.0,
  15965.0,
  13769.0,
  13786.0,
  nan,
  16125.0,
  15081.0,
  nan,
  16863.0,
  15628.0,
  16081.0,
  16525.0,
  16893.0,
  15021.0,
  15021.0,

In [10]:
item_user_history = pd.DataFrame(columns = ["StockCode", "CustomerID_list", "StockCodeID"])
lis = []

for key in dictionary_users: 
    lis.append({"StockCode":key, "CustomerID_list": dictionary_users[key], "StockCodeID": map_stock_values[key] });

item_user_history = item_user_history.append(lis);
print(item_user_history["CustomerID_list"])

dictionary_StockCode = {}

0       [17850.0, 17850.0, 17850.0, 17511.0, 13408.0, ...
1       [17850.0, 17850.0, 17850.0, 17850.0, 17850.0, ...
2       [17850.0, 17850.0, 17850.0, 17850.0, 17850.0, ...
3       [17850.0, 17850.0, 17850.0, 17511.0, 17850.0, ...
4       [17850.0, 17850.0, 17850.0, 17850.0, 17850.0, ...
                              ...                        
4065                                                [nan]
4066                                                [nan]
4067                                            [13790.0]
4068                                                [nan]
4069                                   [16446.0, 16446.0]
Name: CustomerID_list, Length: 4070, dtype: object


In [11]:


group_cleaned =df[['StockCode', 'Quantity', 'CustomerID', 'InvoiceDate']] # Get rid of unnecessary info


grouped_purchased = group_cleaned[group_cleaned['Quantity'] > 0] # Only get customers where purchase totals were positive

In [12]:
grouped_purchased.head()

StockCode  Quantity  CustomerID     InvoiceDate
0    85123A         6     17850.0  12/1/2010 8:26
1     71053         6     17850.0  12/1/2010 8:26
2    84406B         8     17850.0  12/1/2010 8:26
3    84029G         6     17850.0  12/1/2010 8:26
4    84029E         6     17850.0  12/1/2010 8:26

In [13]:
grouped_purchased.head()

StockCode  Quantity  CustomerID     InvoiceDate
0    85123A         6     17850.0  12/1/2010 8:26
1     71053         6     17850.0  12/1/2010 8:26
2    84406B         8     17850.0  12/1/2010 8:26
3    84029G         6     17850.0  12/1/2010 8:26
4    84029E         6     17850.0  12/1/2010 8:26

In [14]:
dictionary_StockCode= {}
dictionary_Quantity = {}
dictionary_InvoiceDate = {}

dictionary_StockCode_testing= {}
dictionary_Quantity_testing = {}
dictionary_InvoiceDate_testing = {}

i = 0; 
grouped_purchased = grouped_purchased.fillna("Nan")
for  rows in grouped_purchased.itertuples():
    if i < 433527:
        dictionary_StockCode[getattr(rows, "CustomerID")] = []
        dictionary_Quantity[getattr(rows, "CustomerID")] = []
        dictionary_InvoiceDate[getattr(rows, "CustomerID")] = [] 
    else:
        dictionary_StockCode_testing[getattr(rows, "CustomerID")] = []
        dictionary_Quantity_testing[getattr(rows, "CustomerID")] = []
        dictionary_InvoiceDate_testing[getattr(rows, "CustomerID")] = []
        
    i += 1; 
        

i  = 0; 

for rows in grouped_purchased.itertuples():
    
    if i < 433527:
        dictionary_StockCode[getattr(rows, "CustomerID")].append(map_stock_values[getattr(rows, "StockCode")])
        dictionary_Quantity[getattr(rows, "CustomerID")].append(getattr(rows, "Quantity"))
        dictionary_InvoiceDate[getattr(rows, "CustomerID")].append(getattr(rows, "InvoiceDate"))
    else:
        dictionary_StockCode_testing[getattr(rows, "CustomerID")].append(map_stock_values[getattr(rows, "StockCode")])
        dictionary_Quantity_testing[getattr(rows, "CustomerID")].append(getattr(rows, "Quantity"))
        dictionary_InvoiceDate_testing[getattr(rows, "CustomerID")].append(getattr(rows, "InvoiceDate"))
    i += 1; 
print(i)

531285


In [15]:
customer_transactions = pd.DataFrame(columns = ["CustomerID", "StockCode", "Quantity", "InvoiceDate"])
lis = []

for key in dictionary_StockCode: 
    lis.append({"CustomerID": key, "StockCode": dictionary_StockCode[key], "Quantity": dictionary_Quantity[key], "InvoiceDate": dictionary_InvoiceDate[key]});

customer_transactions = customer_transactions.append(lis, ignore_index = True, sort = False);

customer_transactions;


In [16]:
customer_transactions_testing = pd.DataFrame(columns = ["CustomerID", "StockCode", "Quantity", "InvoiceDate"])
lis_testing = []

for key in dictionary_StockCode_testing: 
    lis_testing.append({"CustomerID": key, "StockCode": dictionary_StockCode_testing[key], "Quantity": dictionary_Quantity_testing[key], "InvoiceDate": dictionary_InvoiceDate_testing[key]});

customer_transactions_testing = customer_transactions_testing.append(lis_testing, ignore_index = True, sort = False);

print(customer_transactions)
print("----------------------------------------------------------------------------")
print(customer_transactions_testing);


     CustomerID                                          StockCode  \
0       17850.0  [1, 2, 3, 4, 5, 6, 7, 8, 9, 9, 8, 1, 2, 3, 48,...   
1       13047.0  [10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 2...   
2       12583.0  [27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 3...   
3       13748.0  [47, 1971, 1253, 119, 533, 608, 79, 447, 1216,...   
4       15100.0                                       [57, 57, 57]   
...         ...                                                ...   
4030    17387.0  [533, 3434, 3434, 265, 3740, 610, 1141, 3932, ...   
4031    13727.0  [2391, 1354, 80, 406, 33, 438, 189, 661, 342, ...   
4032    13532.0  [3862, 3660, 3170, 3171, 3760, 1214, 590, 413,...   
4033    16445.0  [3738, 621, 3466, 117, 3744, 3747, 3491, 3743,...   
4034    15156.0                             [17, 3982, 3981, 3979]   

                                               Quantity  \
0     [6, 6, 8, 6, 6, 2, 6, 6, 6, 6, 6, 6, 6, 8, 6, ...   
1     [32, 6, 6, 8, 6, 6, 3, 2, 3, 3, 4, 

In [17]:
#print(customer_transactions["StockCode"].map(len))
customer_transactions["StockCode_target"] = customer_transactions["StockCode"].map(lambda x  : x[1:-1])
customer_transactions

maxi = 0; 
for num in customer_transactions["StockCode"].map(len):
    maxi = max(maxi, num)
print(maxi)


108283


In [18]:
#print(customer_transactions["StockCode"].map(len))
customer_transactions_testing["StockCode_target"] = customer_transactions_testing["StockCode"].map(lambda x  : x[1:-1])
customer_transactions_testing

maxi = 0; 
for num in customer_transactions_testing["StockCode"].map(len):
    maxi = max(maxi, num)
print(maxi)


25078


In [19]:
customer_transactions["StockCode_padded"] = tf.keras.preprocessing.sequence.pad_sequences(customer_transactions.StockCode,  maxlen=90, padding='post', value=0, dtype = object).tolist()
customer_transactions.head()

CustomerID                                          StockCode  \
0    17850.0  [1, 2, 3, 4, 5, 6, 7, 8, 9, 9, 8, 1, 2, 3, 48,...   
1    13047.0  [10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 2...   
2    12583.0  [27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 3...   
3    13748.0  [47, 1971, 1253, 119, 533, 608, 79, 447, 1216,...   
4    15100.0                                       [57, 57, 57]   

                                            Quantity  \
0  [6, 6, 8, 6, 6, 2, 6, 6, 6, 6, 6, 6, 6, 8, 6, ...   
1  [32, 6, 6, 8, 6, 6, 3, 2, 3, 3, 4, 4, 6, 3, 3,...   
2  [24, 24, 12, 12, 24, 48, 24, 18, 24, 24, 24, 2...   
3  [80, 2, 2, 2, 2, 12, 12, 12, 40, 1, 12, 6, 40,...   
4                                       [32, 32, 16]   

                                         InvoiceDate  \
0  [12/1/2010 8:26, 12/1/2010 8:26, 12/1/2010 8:2...   
1  [12/1/2010 8:34, 12/1/2010 8:34, 12/1/2010 8:3...   
2  [12/1/2010 8:45, 12/1/2010 8:45, 12/1/2010 8:4...   
3  [12/1/2010 9:00, 4/7/2011 10:13, 4/7/2011 10:1...   
4  [12/1/2010 9:09, 12/8/2010 12:09, 1/10/2011 10...   

                                    StockCode_target  \
0  [2, 3, 4, 5, 6, 7, 8, 9, 9, 8, 1, 2, 3, 48, 49...   
1  [11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 2...   
2  [28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 3...   
3  [1971, 1253, 119, 533, 608, 79, 447, 1216, 533...   
4                                               [57]   

                                    StockCode_padded  
0  [51, 52, 53, 54, 55, 56, 82, 4, 5, 6, 209, 7, ...  
1  [534, 3492, 3471, 3462, 3472, 3456, 3468, 3480...  
2  [366, 367, 3423, 171, 319, 832, 145, 315, 1685...  
3  [47, 1971, 1253, 119, 533, 608, 79, 447, 1216,...  
4  [57, 57, 57, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...

In [20]:
customer_transactions_testing["StockCode_padded"] = tf.keras.preprocessing.sequence.pad_sequences(customer_transactions_testing.StockCode,  maxlen=90, padding='post', value=0, dtype = object).tolist()
customer_transactions_testing.head()

CustomerID                                          StockCode  \
0    15156.0  [325, 3593, 856, 855, 406, 190, 197, 1135, 103...   
1    14963.0  [3882, 3461, 352, 3549, 2153, 554, 3542, 3607,...   
2    16372.0  [21, 2012, 896, 459, 378, 398, 1495, 1448, 635...   
3    17581.0  [61, 593, 1432, 355, 66, 70, 583, 79, 155, 361...   
4    17608.0  [1613, 917, 882, 551, 343, 610, 195, 814, 814,...   

                                            Quantity  \
0  [12, 6, 24, 4, 12, 12, 12, 12, 12, 25, 25, 25,...   
1  [1, 1, 12, 1, 1, 1, 1, 1, 24, 1, 1, 1, 1, 1, 1...   
2  [1, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 2, 1, 2, 4, ...   
3  [10, 10, 20, 20, 12, 25, 6, 12, 4, 12, 8, 8, 8...   
4  [2, 1, 1, 12, 3, 4, 5, 4, 1, 12, 1, 1, 2, 25, ...   

                                         InvoiceDate  \
0  [11/6/2011 12:41, 11/6/2011 12:41, 11/6/2011 1...   
1  [11/6/2011 12:44, 11/6/2011 12:44, 11/6/2011 1...   
2  [11/6/2011 12:50, 11/6/2011 12:50, 11/6/2011 1...   
3  [11/6/2011 12:56, 11/6/2011 12:56, 11/6/2011 1...   
4  [11/6/2011 13:00, 11/6/2011 13:00, 11/6/2011 1...   

                                    StockCode_target  \
0  [3593, 856, 855, 406, 190, 197, 1135, 1031, 68...   
1  [3461, 352, 3549, 2153, 554, 3542, 3607, 1489,...   
2  [2012, 896, 459, 378, 398, 1495, 1448, 635, 39...   
3  [593, 1432, 355, 66, 70, 583, 79, 155, 3612, 3...   
4  [917, 882, 551, 343, 610, 195, 814, 814, 1031,...   

                                    StockCode_padded  
0  [325, 3593, 856, 855, 406, 190, 197, 1135, 103...  
1  [171, 220, 4, 219, 417, 894, 416, 1258, 3768, ...  
2  [1448, 635, 3938, 3175, 3404, 129, 1997, 956, ...  
3  [3676, 3677, 706, 171, 115, 116, 3321, 3326, 6...  
4  [1613, 917, 882, 551, 343, 610, 195, 814, 814,...

In [21]:
customer_transactions["Quantity_padded"] = tf.keras.preprocessing.sequence.pad_sequences(customer_transactions.Quantity,  maxlen=90, padding='post', value=0, dtype = object).tolist()
print(customer_transactions.size)

28245


In [22]:
customer_transactions_testing["Quantity_padded"] = tf.keras.preprocessing.sequence.pad_sequences(customer_transactions_testing.Quantity,  maxlen=90, padding='post', value=0, dtype = object).tolist()
print(customer_transactions_testing.size)

12418


In [23]:
customer_transactions["InvoiceDate_padded"] = tf.keras.preprocessing.sequence.pad_sequences(customer_transactions.InvoiceDate,  maxlen=90, padding='post', value=0, dtype = object).tolist()
customer_transactions.head()
customer_transactions.loc[0]['InvoiceDate']

['12/1/2010 8:26',
 '12/1/2010 8:26',
 '12/1/2010 8:26',
 '12/1/2010 8:26',
 '12/1/2010 8:26',
 '12/1/2010 8:26',
 '12/1/2010 8:26',
 '12/1/2010 8:28',
 '12/1/2010 8:28',
 '12/1/2010 9:01',
 '12/1/2010 9:01',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:02',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:32',
 '12/1/2010 9:34',
 '12/1/2010 9:34',
 '12/1/2010 10:51',
 '12/1/2010 10:51',
 '12/1/2010 10:51',
 '12/1/2010 10:51',
 '12/1/2010 10:51',
 '12/1/2010 10:51',
 '12/1/2010 10:51',
 '12/

In [24]:
customer_transactions_testing["InvoiceDate_padded"] = tf.keras.preprocessing.sequence.pad_sequences(customer_transactions_testing.InvoiceDate,  maxlen=90, padding='post', value=0, dtype = object).tolist()
customer_transactions_testing.head()
customer_transactions_testing.loc[0]['InvoiceDate']

['11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '11/6/2011 12:41',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/5/2011 9:15',
 '12/8/2011 18:22',
 '12/8/2011 18:22',
 '12/8/2011 18:22',
 '12/8/2011 18:22',
 '12/8/2011 18:22',
 '12/8/2011 18:22',
 '12/8/2011 18:22',
 '12/8/2011 18:22',
 '12/8/2011 18:22',
 '12/8/2011 18:22']

In [25]:
print(customer_transactions.size)

32280


In [26]:
print(customer_transactions_testing.size)

14192


In [27]:
''' 
for basket, we can do this, add a new column of "Baskets" to customer_transactions, and then per basket , we can add  new list according to the invoice date. 

'''


def fun(InvoiceDates_list):
    indices_info = [];
    i = 0
    while (i < len(InvoiceDates_list)):
        j = i; 
        while (j < len(InvoiceDates_list) and InvoiceDates_list[i] == InvoiceDates_list[j]):
            j += 1; 
        indices_info.append([i, j]);
        i = j

    return indices_info


customer_transactions["Basket_Indices"] = customer_transactions["InvoiceDate"].map(lambda x: fun(x));
print(customer_transactions.head());

  CustomerID                                          StockCode  \
0    17850.0  [1, 2, 3, 4, 5, 6, 7, 8, 9, 9, 8, 1, 2, 3, 48,...   
1    13047.0  [10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 2...   
2    12583.0  [27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 3...   
3    13748.0  [47, 1971, 1253, 119, 533, 608, 79, 447, 1216,...   
4    15100.0                                       [57, 57, 57]   

                                            Quantity  \
0  [6, 6, 8, 6, 6, 2, 6, 6, 6, 6, 6, 6, 6, 8, 6, ...   
1  [32, 6, 6, 8, 6, 6, 3, 2, 3, 3, 4, 4, 6, 3, 3,...   
2  [24, 24, 12, 12, 24, 48, 24, 18, 24, 24, 24, 2...   
3  [80, 2, 2, 2, 2, 12, 12, 12, 40, 1, 12, 6, 40,...   
4                                       [32, 32, 16]   

                                         InvoiceDate  \
0  [12/1/2010 8:26, 12/1/2010 8:26, 12/1/2010 8:2...   
1  [12/1/2010 8:34, 12/1/2010 8:34, 12/1/2010 8:3...   
2  [12/1/2010 8:45, 12/1/2010 8:45, 12/1/2010 8:4...   
3  [12/1/2010 9:00, 4/7/2011 10:13, 

In [28]:

customer_transactions_testing["Basket_Indices"] = customer_transactions_testing["InvoiceDate"].map(lambda x: fun(x));
print(customer_transactions_testing.head());

  CustomerID                                          StockCode  \
0    15156.0  [325, 3593, 856, 855, 406, 190, 197, 1135, 103...   
1    14963.0  [3882, 3461, 352, 3549, 2153, 554, 3542, 3607,...   
2    16372.0  [21, 2012, 896, 459, 378, 398, 1495, 1448, 635...   
3    17581.0  [61, 593, 1432, 355, 66, 70, 583, 79, 155, 361...   
4    17608.0  [1613, 917, 882, 551, 343, 610, 195, 814, 814,...   

                                            Quantity  \
0  [12, 6, 24, 4, 12, 12, 12, 12, 12, 25, 25, 25,...   
1  [1, 1, 12, 1, 1, 1, 1, 1, 24, 1, 1, 1, 1, 1, 1...   
2  [1, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 2, 1, 2, 4, ...   
3  [10, 10, 20, 20, 12, 25, 6, 12, 4, 12, 8, 8, 8...   
4  [2, 1, 1, 12, 3, 4, 5, 4, 1, 12, 1, 1, 2, 25, ...   

                                         InvoiceDate  \
0  [11/6/2011 12:41, 11/6/2011 12:41, 11/6/2011 1...   
1  [11/6/2011 12:44, 11/6/2011 12:44, 11/6/2011 1...   
2  [11/6/2011 12:50, 11/6/2011 12:50, 11/6/2011 1...   
3  [11/6/2011 12:56, 11/6/2011 12:56

In [29]:
dictionary_customers_baskets = {}
dictionary_customers_lens = {}
users_info = {}

for row in customer_transactions.itertuples():
    user = getattr(row, "CustomerID")
    baskets = getattr(row, "StockCode_padded")
    indices = getattr(row, "Basket_Indices")
    if not (user in dictionary_customers_baskets):
        dictionary_customers_baskets[user] = []
        dictionary_customers_lens[user] = []
        users_info[user] = user
    for num in indices:
        if (len(baskets[num[0]:num[1]]) == 0):
            continue;
        dictionary_customers_baskets[user].append(baskets[num[0]: num[1]])
        dictionary_customers_lens[user].append(num[1] - num[0])
        users_info[user] = user
    if (len(dictionary_customers_baskets[user]) == 0):
        del dictionary_customers_baskets[user]
        del dictionary_customers_lens[user]
        del users_info[user]
users_baskets_list = list(dictionary_customers_baskets.values())
users_lens_list = list(dictionary_customers_lens.values())
users_info = list(users_info.values())


data_2  = []
for user in users_info:
    baskets = dictionary_customers_baskets[user]
    lens  = dictionary_customers_lens[user]
    data_2.append([user, baskets, lens])
print(data_2)


[[17850.0, [[51, 52, 53, 54, 55, 56, 82], [4, 5], [6, 209], [7, 9, 8, 1, 2, 3, 104, 48, 49, 50, 51, 52, 53, 54, 55, 56], [82, 4, 5, 6, 209, 7, 9, 8, 1, 2, 3, 104, 48, 49, 50, 51], [52, 53], [54, 55, 56, 82, 4, 5, 6, 209, 7, 9, 8, 1, 2, 3, 49, 50, 51, 52], [55, 56], [4, 5, 6, 7, 8, 9, 1, 2, 3, 104, 48, 49, 51, 52, 53, 54, 55], [56, 4], [5, 6, 209, 7, 9, 8]], [7, 2, 2, 16, 16, 2, 18, 2, 17, 2, 12]], [13047.0, [[534, 3492, 3471, 3462, 3472, 3456, 3468, 3480, 3476, 3549, 3542, 3446, 3448, 3547, 3600, 3602], [3603], [3601, 1298, 808, 1580, 744, 1, 19, 1647, 533, 15, 3170, 605, 2612, 3359, 3384, 3381, 16, 1598, 18, 19, 1520, 1573, 21, 3471, 3472, 3462], [3468, 3601, 3547, 3542, 3448, 3549, 3162, 3409, 3408, 22, 3698, 3701, 2913, 2612, 2336, 1484, 396, 3823, 22, 2611], [2612, 605, 1614, 896, 756, 21, 3600, 3602, 1298, 3547, 416, 417, 3864, 3870, 3856, 3631, 3675, 3677, 3650], [3889, 3787, 3457, 3937, 3469, 3826, 47, 228]], [16, 1, 26, 20, 19, 32]], [12583.0, [[366, 367, 3423, 171, 319, 832, 1

In [30]:
dictionary_customers_baskets_testing = {}
dictionary_customers_lens_testing = {}
users_info_testing = {}

for row in customer_transactions_testing.itertuples():
    user = getattr(row, "CustomerID")
    baskets = getattr(row, "StockCode_padded")
    indices = getattr(row, "Basket_Indices")
    if not (user in dictionary_customers_baskets_testing):
        dictionary_customers_baskets_testing[user] = []
        dictionary_customers_lens_testing[user] = []
        users_info_testing[user] = user
    for num in indices:
        if (len(baskets[num[0]:num[1]]) == 0):
            continue;
        dictionary_customers_baskets_testing[user].append(baskets[num[0]: num[1]])
        dictionary_customers_lens_testing[user].append(num[1] - num[0])
        users_info_testing[user] = user
    if (len(dictionary_customers_baskets_testing[user]) == 0):
        del dictionary_customers_baskets_testing[user]
        del dictionary_customers_lens_testing[user]
        del users_info_testing[user]
users_baskets_list_testing = list(dictionary_customers_baskets_testing.values())
users_lens_list_testing = list(dictionary_customers_lens_testing.values())
users_info_testing = list(users_info_testing.values())


data_2_testing  = []
for user in users_info_testing:
    baskets = dictionary_customers_baskets_testing[user]
    lens  = dictionary_customers_lens_testing[user]
    data_2_testing.append([user, baskets, lens])
print(data_2_testing)


[[15156.0, [[325, 3593, 856, 855, 406, 190, 197, 1135, 1031, 685, 1480, 1536, 3691, 1790, 1109, 586], [575, 577, 578, 507, 1109, 751, 555, 1174, 3620, 1445, 1332, 1331, 655, 4064, 4063, 1010, 1651, 96, 654, 695, 858, 657, 579, 574, 576], [438, 33, 189, 858, 657, 1445, 1333, 6, 4053, 3997]], [16, 25, 10]], [14963.0, [[171, 220, 4, 219, 417, 894, 416, 1258, 3768, 3453, 761, 3549, 2153, 3532, 3676, 352, 1848, 849, 3965, 3872, 170, 3530, 260, 3543, 872, 3553, 398, 3461, 2423, 609, 566, 3673, 260, 3575, 3607, 3432, 171, 3853, 633, 554, 894, 3487, 1521, 795, 1864, 847, 1083, 1082, 3457, 2504, 2728, 1753, 1560, 2192, 1559, 1531, 3453, 3859, 446, 666, 3241, 3559, 3986, 3607, 3453, 4060, 4062], [3164, 3445, 3444, 3560, 127, 3987, 3323, 4024, 267, 3325, 3323, 295, 3327, 894, 417, 620, 705, 3553, 3542, 3593, 3241, 3559, 171]], [67, 34]], [16372.0, [[1448, 635, 3938, 3175, 3404, 129, 1997, 956, 411, 1683, 499, 264, 499, 856, 370, 1562, 1109, 430, 342, 431, 188, 144, 186, 427, 635, 199, 958, 772, 5

In [31]:
X= []
y = []
for rows in customer_transactions.itertuples():
    r = []
    r= (getattr(rows, "StockCode_padded"))
#    r.append(getattr(rows, "Quantity_padded"))
 #   r.append(getattr(rows, "InvoiceDate_padded"))
    if (len(r) != 0) and (len(getattr(rows, "StockCode_target")) != 0):
        X.append(r);
        y.append(getattr(rows, "StockCode_target")[-1])
X = np.array(X);
y = np.array(y);
print(X)
print(y)
print(X.shape)
print(y.shape)

[[  51   52   53 ...    7    9    8]
 [ 534 3492 3471 ... 3826   47  228]
 [ 366  367 3423 ...  171   46  989]
 ...
 [3862 3660 3170 ...    0    0    0]
 [3738  621 3466 ...    0    0    0]
 [  17 3982 3981 ...    0    0    0]]
[   9   47   46 ...  106   82 3981]
(3914, 90)
(3914,)


In [32]:
X= []
y = []
for rows in customer_transactions_testing.itertuples():
    r = []
    r= (getattr(rows, "StockCode_padded"))
#    r.append(getattr(rows, "Quantity_padded"))
 #   r.append(getattr(rows, "InvoiceDate_padded"))
    if (len(r) != 0) and (len(getattr(rows, "StockCode_target")) != 0):
        X.append(r);
        y.append(getattr(rows, "StockCode_target")[-1])
X = np.array(X);
y = np.array(y);
print(X)
print(y)
print(X.shape)
print(y.shape)

[[ 325 3593  856 ...    0    0    0]
 [ 171  220    4 ... 3241 3559  171]
 [1448  635 3938 ...  406  761 3784]
 ...
 [  35  362 3324 ...    0    0    0]
 [  46  500  248 ...    0    0    0]
 [  38  180  691 ...    0    0    0]]
[4053 3559  761 ... 1614 3517 3316]
(1702, 90)
(1702,)


In [33]:
from tensorflow.keras import *


n_steps = 1
n_features = 90
X = X.reshape(X.shape[0], X.shape[1], 1)

print(X.shape)

    

(1702, 90, 1)


In [35]:
def pool_avg(tensor, dim):
    return torch.avg(tensor, dim)[0]
def pool_max(tensor, dim):
    return torch.max(tensor, dim)[0]

config = {
    'basket_pool_type': 'max', # 'avg'
                'rnn_layers': 2,  # 2, 3
                'rnn_type': 'RNN_RELU',  #'RNN_TANH',#'GRU',#'LSTM',# 'RNN_RELU',
                'dropout': 0.5,
                # 'num_product': 49688 + 1, # padding idx = 0
                'num_product': 4071, 
                # 49688 products, padding idx = 0, none idx = 49689, none idx indicates no products
                'none_idx': 49689,
                'embedding_dim': 128, # 128
                'cuda': True, # True,
                'clip': 200,  # 0.25
                'epochs': 100,
                'batch_size': 32,
                'learning_rate': 0.001, # 0.0001
                'log_interval': 1, # num of batchs between two logging
                'checkpoint_dir': '\dream-{epoch:02d}-{loss:.4f}.model',
}

GPUS = "5,3,2,4"
REORDER = False
RAW_DATA_DIR = './'
FEAT_DATA_DIR = './'
DREAM_MODEL_DIR = './'

DREAM_CONFIG = {'basket_pool_type': 'max', # 'avg'
                'rnn_layers': 2,  # 2, 3
                'rnn_type': 'RNN_RELU',  #'RNN_TANH',#'GRU',#'LSTM',# 'RNN_RELU',
                'dropout': 0.5,
                # 'num_product': 49688 + 1, # padding idx = 0
                'num_product': 4070 + 1, 
                # 49688 products, padding idx = 0, none idx = 49689, none idx indicates no products
                'none_idx': 49689,
                'embedding_dim': 128, # 128
                'cuda': True, # True,
                'clip': 200,  # 0.25
                'epochs': 100,
                'batch_size': 32,
                'learning_rate': 0.001, # 0.0001
                'log_interval': 1, # num of batchs between two logging
                'checkpoint_dir': DREAM_MODEL_DIR + '\dream-{epoch:02d}-{loss:.4f}.model',
                }

"""
 configure DREAM
 
 @TODO: REFACTOR config class
"""
       
class Config(object):
    def __init__(self, config):
        self.cuda = config['cuda']
        self.clip = config['clip']
        self.epochs = config['epochs']
        self.batch_size = config['batch_size']
        self.learning_rate = config['learning_rate'] # Initial Learning Rate
        self.log_interval = config['log_interval']
        
        self.none_idx = config['none_idx']
        # self.pn_pair_num = config['pn_pair_num']
        self.basket_pool_type = config['basket_pool_type']
        self.rnn_type = config['rnn_type']
        self.rnn_layer_num = config['rnn_layers']
        self.dropout = config['dropout']
        self.num_product = config['num_product'] # 商品数目，用于定义Embedding Layer
        self.embedding_dim = config['embedding_dim'] # 商品表述维数， 用于定义Embedding Layer
        self.checkpoint_dir = config['checkpoint_dir']

        self.alias = '{}{}_{}_{}_{}_clip{}'.format(self.rnn_layer_num,
                                                   self.rnn_type,
                                                   self.embedding_dim,
                                                   self.learning_rate,
                                                   self.batch_size,
                                                   self.clip)
        
dr_config = Config(DREAM_CONFIG)



In [36]:
#only model related functions


def get_grad_norm(model):
    grads = []
    for p in model.parameters():
        if p.grad is not None:
            grads.append(p.grad.data.view(-1, 1))
    assert len(grads) > 0
    return torch.norm(torch.cat(grads))

def repackage_hidden(h):
    """Wraps hidden states in new Variables, to detach them from their history."""
    if type(h) == Variable:
        return Variable(h.data)
    else:
        return tuple(repackage_hidden(v) for v in h)

def get_ratio_update(delta, weight):
    delta = torch.cat([d.data.view(-1, 1) for d in delta])
    weight = torch.cat([w.data.view(-1, 1) for w in weight])
    return torch.norm(delta) / torch.norm(weight)


def get_weight_update(previous_weight, weight):
    """
    args:
        previous_weight: list"""
    deltas = []
    for i, w in enumerate(weight):
        deltas.append(w - previous_weight[i])
    return deltas

def bpr_loss(x, dynamic_user, item_embedding, config):
    '''
        bayesian personalized ranking loss for implicit feedback
        parameters:
        - x: batch of users' baskets
        - dynamic_user: batch of users' dynamic representations
        - item_embedding: item_embedding matrix
        - config: model configuration
    '''
    nll = 0
    ub_seqs = []
    for u, du in zip(x, dynamic_user):
        du_p_product = torch.mm(du, item_embedding.t())  # shape: max_len, num_item
        nll_u = []  # nll for user
        print(u)
        for t, basket_t in enumerate(u):
            if basket_t[0] != 0 and t != 0:
                pos_idx = torch.cuda.LongTensor(basket_t) if config.cuda else torch.LongTensor(basket_t)
                # Sample negative products
                neg = [random.choice(range(1, config.num_product)) for _ in range(len(basket_t))]  # replacement
                # neg = random.sample(range(1, config.num_product), len(basket_t)) # without replacement
                neg_idx = torch.cuda.LongTensor(neg) if config.cuda else torch.LongTensor(neg)
                # Score p(u, t, v > v')
                score = du_p_product[t - 1][pos_idx] - du_p_product[t - 1][neg_idx]
                # Average Negative log likelihood for basket_
                
                nll_u.append(- torch.mean(torch.nn.LogSigmoid()(score)))
        nll += torch.mean(torch.cat(nll_u))
    return nll



In [37]:
pip install tensorboardX

Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\python39\python.exe -m pip install --upgrade pip' command.


In [38]:

from tensorboardX import SummaryWriter


writer = SummaryWriter(log_dir='runs/{}'.format(dr_config.alias))  # tensorboard writer
writer.add_text('config', str(dr_config))
best_val_loss = None

In [39]:
# -*- coding: utf-8 -*-
"""
    DREAM: Dynamic Recurrent Network for Next Basket Prediction
    Based on PyTorch
    
    @TODO: 
        - Efficiency Variabel Usage
        - Other initilizations for item/product embedding, for example LDA
"""
import random
import numpy as np

import torch
from torch.autograd import Variable


class DreamModel(torch.nn.Module):
    """       Input Data: b_1, ... b_i ..., b_t
                   b_i stands for user u's ith basket
                   b_i = [p_1,..p_j...,p_n]
                   p_j stands for the  jth product in user u's ith basket
    """
    
    def __init__(self, config):
        super(DreamModel, self).__init__()
        # Model configuration
        self.config = config
        # Layer definitons
        self.encode = torch.nn.Embedding(config.num_product, 
                                         config.embedding_dim,
                                         padding_idx = 0) # Item embedding layer, 商品编码
        self.pool = {'avg':pool_avg, 'max':pool_max}[config.basket_pool_type] # Pooling of basket
        # RNN type specify
        if config.rnn_type in ['LSTM', 'GRU']:
            self.rnn = getattr(torch.nn, config.rnn_type)(config.embedding_dim, 
                                                          config.embedding_dim, 
                                                          config.rnn_layer_num, 
                                                          batch_first=True, 
                                                          dropout=config.dropout)
        else:
            nonlinearity = {'RNN_TANH': 'tanh', 'RNN_RELU': 'relu'}[config.rnn_type]
            self.rnn = torch.nn.RNN(config.embedding_dim, 
                                    config.embedding_dim, 
                                    config.rnn_layer_num, 
                                    nonlinearity=nonlinearity, 
                                    batch_first=True, 
                                    dropout=config.dropout)
    
    def forward(self, data, lengths, hidden):
        # Basket Encoding 
        ub_seqs = [] # users' basket sequence
        for user in data: # x shape (batch of user, time_step, indice of product) nested lists
            embed_baskets = []
#             print("TTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTTT")
#             print(user)
            
            for basket in user:                
                basket = torch.LongTensor(basket).resize_(1, len(basket))
                basket = self.encode(torch.autograd.Variable(basket)) # shape: 1, len(basket), embedding_dim
                embed_baskets.append(self.pool(basket, dim=1))
            
            # concat current user's all baskets and append it to users' basket sequence
            while (len(embed_baskets) < 100):
                embed_baskets.append(torch.zeros(1, 128))
            ub_seqs.append(torch.cat(embed_baskets, 0).unsqueeze(0))  # shape: 1, num_basket, embedding_dim
#         print(ub_seqs[0].size()) # 1, 10, 128
#         for num in ub_seqs:
#             if (num.size()[1] < 100):
#                 while (num.size()[1] < 100):
#                     num.append(torch.zeros(1, 128))
#         print(len(ub_seqs)) #32
        # Input for rnn 
        ub_seqs = torch.cat(ub_seqs, 0) # shape: batch_size, max_len, embedding_dim
#         print(ub_seqs)
#         print(ub_seqs.size()) 
        
#         packed_ub_seqs = torch.nn.utils.rnn.pack_padded_sequence(ub_seqs, lengths, batch_first=True) # packed sequence as required by pytorch
        
        # RNN
        output, h_u = self.rnn(ub_seqs, hidden)
      #  dynamic_user, _ = torch.nn.utils.rnn.pad_packed_sequence(output, batch_first=True) # shape: batch_size, max_len, embedding_dim
        return output, h_u

    
    def init_weight(self):
        # Init item embedding
        initrange = 0.1
        self.encode.weight.data.uniform_(-initrange, initrange)
    
    def init_hidden(self, batch_size):
        # Init hidden states for rnn
        weight = next(self.parameters()).data
        if self.config.rnn_type == 'LSTM':
            return (Variable(weight.new(self.config.rnn_layer_num, batch_size, self.config.embedding_dim).zero_()),
                    Variable(weight.new(self.config.rnn_layer_num, batch_size, self.config.embedding_dim).zero_()))
        else:
            return Variable(weight.new(self.config.rnn_layer_num, batch_size, self.config.embedding_dim).zero_())   
   

In [40]:
from copy import deepcopy
dr_model =  DreamModel(dr_config)


optim = torch.optim.Adam(dr_model.parameters(), lr = dr_config.learning_rate)


# print(final_data)
def pad_batch_of_lists(batch_of_lists, max_len):
    '''
        pad batch of lists
    '''
    padded = [l + [0] * (max_len - len(l)) for l in batch_of_lists]
    return padded

def pad_batch_of_lists_2(batch_of_lists, max_len):
    '''
        pad batch of lists
    '''
    padded = batch_of_lists
    for i in range (4071):
        padded.append(0)
    return padded


def batchify(data, batch_size, is_reordered = False):
        num_batch = len(data) // batch_size
        for i in range(num_batch):
        #    print(data[i * batch_size : (i + 1) * batch_size])
            t = data[i * batch_size : (i + 1) * batch_size]

            yield t
        u = num_batch*batch_size
        if len(data) % batch_size != 0:
            t = data[u : ]
#             print(residual)
          #  print(baskets)
#             baskets, lens, uids = sort_batch_of_lists(baskets, lens, uids)
#             padded_baskets = pad_batch_of_lists(baskets, 4071)
#             padded_lens = pad_batch_of_lists_2(lens, 4071)
#             padded_uids = pad_batch_of_lists_2(uids, 4071)
            yield t
# # print(data)
# print(len(data[0]))
# for k in (batchify(data, 32)):
#     print(k, "OOOO \n")

def bpr_loss(x, dynamic_user, item_embedding, config):
    '''
        bayesian personalized ranking loss for implicit feedback
        parameters:
        - x: batch of users' baskets
        - dynamic_user: batch of users' dynamic representations
        - item_embedding: item_embedding matrix
        - config: model configuration
    '''
    nll = 0
    ub_seqs = []
#     print("BPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPRBPR")
    nll = 0
    ub_seqs = []
    for u, du in zip(x, dynamic_user):
        du_p_product = torch.mm(du, item_embedding.t())  # shape: max_len, num_item
#         print(du_p_product.size())
        nll_u = []  # nll for user
        for t, basket_t in enumerate(u):
#             print(t)
#             print(basket_t)
            if basket_t[0] != 0 and t != 0:
                pos_idx = torch.LongTensor(basket_t)
                # Sample negative products
                neg = [random.choice(range(1, config.num_product)) for _ in range(len(basket_t))]  # replacement
                # neg = random.sample(range(1, config.num_product), len(basket_t)) # without replacement
                neg_idx = torch.LongTensor(neg) 
                # Score p(u, t, v > v')
                score = du_p_product[0][pos_idx] - du_p_product[0][neg_idx]
                # Average Negative log likelihood for basket_t
                nll_u.append(- torch.mean(torch.nn.LogSigmoid()(score)))
#                 print(nll_u)
        try:
#             print(torch.mean(torch.cat(nll_u)))
            nll += torch.mean(torch.cat(nll_u))
        except:
            for num in nll_u:
                nll += num
#     print(type(nll))
    return nll

def train_dream(train_ub):
    dr_model.train()  # turn on training mode for dropout
    dr_hidden = dr_model.init_hidden(32)
    total_loss = 0
    start_time = time()
    num_batchs = ceil(len(train_ub) / dr_config.batch_size)
    a = 0
    for x in (batchify(train_ub, dr_config.batch_size)):
        a += 32
        if (len(x) != 32):
            break
#         print("BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB")
#         print(x,"OOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOO  \n")
        baskets = []
        lens = []
        for num in x:
            baskets.append(num[1])
            lens.append(num[2])
#         dr_hidden = repackage_hidden(dr_hidden)  # repackage hidden state for RNN
        dr_model.zero_grad()  # optim.zero_grad()
        dynamic_user, _ = dr_model(baskets,lens,  dr_hidden)
#         print(dynamic_user.size())
#         print("-----------------------------------------------------------------------------")
        loss = bpr_loss(baskets, dynamic_user, dr_model.encode.weight, dr_config)
#         print(loss)
        loss.backward()

        # Clip to avoid gradient exploding
        torch.nn.utils.clip_grad_norm(dr_model.parameters(), dr_config.clip)

        # Parameter updating
        # manual SGD
        # for p in dr_model.parameters(): # Update parameters by -lr*grad
        #    p.data.add_(- dr_config.learning_rate, p.grad.data)
        # adam
        grad_norm = get_grad_norm(dr_model)
        previous_params = deepcopy(list(dr_model.parameters()))
        optim.step()

        total_loss += loss.data
        params = deepcopy(list(dr_model.parameters()))
        delta = get_weight_update(previous_params, params)
        weight_update_ratio = get_ratio_update(delta, params)
        print(total_loss)
        # Logging
        if i % dr_config.log_interval == 0 and i > 0:
            elapsed = (time() - start_time) * 1000 / dr_config.log_interval
            cur_loss = total_loss.item()/ dr_config.log_interval / dr_config.batch_size  # turn tensor into float
            total_loss = 0
            start_time = time()
            print(
                '[Training]| Epochs {:3d} | Batch {:5d} / {:5d} | ms/batch {:02.2f} | Loss {:05.2f} |'.format(epoch, i,
                                                                                                              num_batchs,
                                                                                                              elapsed,
                                                                                                              cur_loss))
            writer.add_scalar('model/train_loss', cur_loss, epoch * num_batchs + i)
            writer.add_scalar('model/grad_norm', grad_norm, epoch * num_batchs + i)
            writer.add_scalar('model/weight_update_ratio', weight_update_ratio, epoch * num_batchs + i)

In [41]:

def eval_batch(dr_model, ub, up, batch_size, is_reordered = False):
    '''
        Using dr_model to predict (u,p) score in batch
        Parameters:
        - ub: users' baskets
        - up: users' history purchases
        - batch_size
    '''
    # turn on evaluation mode
    dr_model.eval()
    is_cuda =  dr_model.config.cuda
    item_embedding = dr_model.encode.weight
    dr_hidden = dr_model.init_hidden(batch_size)

    id_u, item_u, score_u, dynam_u = [], [], [], []
    start_time = time()
    num_batchs = ceil(len(ub) / batch_size)
    for i, x in enumerate(batchify(ub, batch_size, is_reordered)):
        if is_reordered is True:
            baskets, lens, uids, r_baskets, h_baskets = x
        else:
            baskets, lens, uids = x
        dynamic_user, _ = dr_model(baskets, lens, dr_hidden)
        for uid, l, du in zip(uids, lens, dynamic_user):
            du_latest =  du[l - 1].unsqueeze(0)
            # calculating <u,p> score for all history <u,p> pair 
            history_item = [int(i) for i in up[up.user_id == uid]['product_id'].values[0]]
            history_item = torch.cuda.LongTensor(history_item) if is_cuda else torch.LongTensor(history_item)
            score_up = torch.mm(du_latest, item_embedding[history_item].t()).cpu().data.numpy()[0]
            id_u.append(uid), dynam_u.append(du_latest.cpu().data.numpy()[0]), item_u.append(history_item.cpu().numpy()),score_u.append(score_up)
        # Logging
        elapsed = time() - start_time; start_time = time()
        print('[Predicting]| Batch {:5d} / {:5d} | seconds/batch {:02.02f}'.format(i, num_batchs, elapsed))
    return id_u, item_u, score_u, dynam_u


def eval_up(uid, pid, dr_model, ub, dr_hidden):
    '''
        calculate latest score for (u,p) pair
        ub for single user
        dr_hidden: should be initialized and repackage after each batch
    '''
    dynamic_user = get_dynamic_u(uid, dr_model, ub, dr_hidden)
    item_embedding = get_item_embedding(pid, dr_model)
    score_up = torch.mm(dynamic_user, item_embedding.t())
    return score_up

def get_dynamic_u(uid, dr_model, ub, dr_hidden):
    '''
        get latest dynamic representation of user uid
        dr_hidden must be provided as global variable
    '''
    for i,x in enumerate(batchify(ub, 1)):
        baskets, lens, uids = x
        _, dynamic_user, _ = dr_model(baskets, lens, dr_hidden)
    return dynamic_user[0][lens[0] - 1].unsqueeze(0)

def get_item_embedding(pid, dr_model):
    '''
        get item's embedding
        pid can be a integer or a torch.cuda.LongTensor
    '''
    if isinstance(pid, torch.cuda.LongTensor) or isinstance(pid, torch.LongTensor):
        return dr_model.encode.weight[pid]
    elif isinstance(pid, int):
        return dr_model.encode.weight[pid].unsqueeze(0)
    else:
        print('Unsupported Index Type %s'%type(pid))
        return None
    

In [43]:
def eval_pred(dr_model, ub):
    '''
        evaluate dream model for predicting next basket on all training users
        in batches
    '''
    item_embedding = dr_model.encode.weight
    dr_model.eval()
    dr_hidden = dr_model.init_hidden(dr_model.config.batch_size)
    start_time = time()
    id_u, score_u = [], [] # user's id, user's score
    num_batchs = ceil(len(ub) / dr_model.config.batch_size)
    for i,x in enumerate(batchify(ub, dr_model.config.batch_size)):
#         print(i)
        baskets, lens, uids = x
        _, dynamic_user, _ = dr_model(baskets, lens, dr_hidden)# shape: batch_size, max_len, embedding_size
        dr_hidden = repackage_hidden(dr_hidden)
        for i,l,du in zip(uids, lens, dynamic_user):
            du_latest = du[l - 1].unsqueeze(0) # shape: 1, embedding_size
            score_up = torch.mm(du_latest, item_embedding.t()) # shape: 1, num_item
            score_u.append(score_up.cpu().data.numpy())
            id_u.append(i)
    elapsed = time() - start_time 
    print('[Predicting] Elapsed: {02.2f}'.format(elapsed))
    return score_ub, id_u


In [44]:
'''
def train_dream(train_ub):
    dr_model.train()  # turn on training mode for dropout
    dr_hidden = dr_model.init_hidden(32)
    total_loss = 0
    start_time = time()
    num_batchs = ceil(len(train_ub) / dr_config.batch_size)
    a = 0
    for x in (batchify(train_ub, dr_config.batch_size)):
        a += 32
        if (len(x) != 32):
            break
        print("BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB")
        print(x,"OOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOO  \n")
        baskets = []
        lens = []
        for num in x:
            baskets.append(num[1])
            lens.append(num[2])
#         dr_hidden = repackage_hidden(dr_hidden)  # repackage hidden state for RNN
        dr_model.zero_grad()  # optim.zero_grad()
        dynamic_user, _ = dr_model(baskets,lens,  dr_hidden)
        print(dynamic_user.size())
        print("-----------------------------------------------------------------------------")
        loss = bpr_loss(baskets, dynamic_user, dr_model.encode.weight, dr_config)
        print(loss)
        loss.backward()

        # Clip to avoid gradient exploding
        torch.nn.utils.clip_grad_norm(dr_model.parameters(), dr_config.clip)

        # Parameter updating
        # manual SGD
        # for p in dr_model.parameters(): # Update parameters by -lr*grad
        #    p.data.add_(- dr_config.learning_rate, p.grad.data)
        # adam
        grad_norm = get_grad_norm(dr_model)
        previous_params = deepcopy(list(dr_model.parameters()))
        optim.step()

        total_loss += loss.data
        params = deepcopy(list(dr_model.parameters()))
        delta = get_weight_update(previous_params, params)
        weight_update_ratio = get_ratio_update(delta, params)
        print(total_loss)
        # Logging
        if i % dr_config.log_interval == 0 and i > 0:
            elapsed = (time() - start_time) * 1000 / dr_config.log_interval
            cur_loss = total_loss.item()/ dr_config.log_interval / dr_config.batch_size  # turn tensor into float
            total_loss = 0
            start_time = time()
            print(
                '[Training]| Epochs {:3d} | Batch {:5d} / {:5d} | ms/batch {:02.2f} | Loss {:05.2f} |'.format(epoch, i,
                                                                                                              num_batchs,
                                                                                                              elapsed,
                                                                                                              cur_loss))
            writer.add_scalar('model/train_loss', cur_loss, epoch * num_batchs + i)
            writer.add_scalar('model/grad_norm', grad_norm, epoch * num_batchs + i)
            writer.add_scalar('model/weight_update_ratio', weight_update_ratio, epoch * num_batchs + i)

'''
'''


'''

def evaluate_dream(test_ub):
    dr_model.eval()
    dr_hidden = dr_model.init_hidden(32)

    total_loss = 0
    start_time = time()
    num_batchs = ceil(len(test_ub) / dr_config.batch_size)
    a = 0
    for  x in (batchify(test_ub, dr_config.batch_size)):
        a += 32
        if (len(x) != 32):
            break;
#         print("BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB")
#         print(x,"OOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOO  \n")
        baskets = []
        lens = []
        for num in x:
            baskets.append(num[1])
            lens.append(num[2])
        dynamic_user, _ = dr_model(baskets, lens, dr_hidden)
        loss = bpr_loss(baskets, dynamic_user, dr_model.encode.weight, dr_config)
#         dr_hidden = repackage_hidden(dr_hidden)
        total_loss += loss.data

    # Logging
    elapsed = (time() - start_time) * 1000 / num_batchs
    total_loss = total_loss.item() / num_batchs / dr_config.batch_size
    writer.add_scalar('model/eval_loss', total_loss, (epoch + 1) * num_batchs)
    writer.add_scalar('model/eval_loss', total_loss, (epoch + 1) * num_batchs)
    print('[Evaluation]| Epochs {:3d} | Elapsed {:02.2f} | Loss {:05.2f} |'.format(epoch, elapsed, total_loss))

    return total_loss


def evaluate_reorder_dream():
    dr_model.eval()
    dr_hidden = dr_model.init_hidden(dr_config.batch_size)

    total_loss = 0
    start_time = time()
    num_batchs = ceil(len(test_ub) / dr_config.batch_size)
    for  x in (batchify(test_ub, dr_config.batch_size, is_reordered=True)):
        baskets, lens, _, r_baskets, h_baskets = x
        dynamic_user, _ = dr_model(baskets, lens, dr_hidden)
        loss = reorder_bpr_loss(r_baskets, h_baskets, dynamic_user, dr_model.encode.weight, dr_config)
        dr_hidden = repackage_hidden(dr_hidden)
        total_loss += loss.data

    # Logging
    elapsed = (time() - start_time) * 1000 / num_batchs
    total_loss = total_loss.item()/ num_batchs / dr_config.batch_size
    print('[Evaluation]| Epochs {:3d} | Elapsed {:02.2f} | Loss {:05.2f} |'.format(epoch, elapsed, total_loss))
    return total_loss



In [47]:

REORDER = False
try:
    for k,v in DREAM_CONFIG.items():
        print(k,v)
    # training
    for epoch in range(5):
        if REORDER:
            train_reorder_dream()
        else:
            print("////////////////////////////////////////////////////////////////////////////////////////////////////////////////////")
#             print(data)
        
            train_dream(data_2)
        print('-' * 89)
        if REORDER:
            val_loss = evaluate_reorder_dream()
        else:
            val_loss = evaluate_dream(data_2_testing)
        print('-' * 89)
        # checkpoint
        if not best_val_loss or val_loss < best_val_loss:
            with open(dr_config.checkpoint_dir.format(epoch = epoch, loss = val_loss), 'wb') as f:
                torch.save(dr_model, f)
            best_val_loss = val_loss
        else:
            # Manual SGD slow down lr if no improvement in val_loss
            # dr_config.learning_rate = dr_config.learning_rate / 4
            pass
except KeyboardInterrupt:
    print('*' * 89)
    print('Early Stopping!')

basket_pool_type max
rnn_layers 2
rnn_type RNN_RELU
dropout 0.5
num_product 4071
none_idx 49689
embedding_dim 128
cuda True
clip 200
epochs 100
batch_size 32
learning_rate 0.001
log_interval 1
checkpoint_dir ./\dream-{epoch:02d}-{loss:.4f}.model
////////////////////////////////////////////////////////////////////////////////////////////////////////////////////


<ipython-input-40-fb0ef03f107a>:117: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  torch.nn.utils.clip_grad_norm(dr_model.parameters(), dr_config.clip)


tensor(92.3806)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 3145.58 | Loss 02.89 |
tensor(57.0547)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 2246.64 | Loss 01.78 |
tensor(75.4982)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 2379.91 | Loss 02.36 |
tensor(68.7695)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 2005.85 | Loss 02.15 |
tensor(79.8563)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 2321.30 | Loss 02.50 |
tensor(81.3423)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 2312.19 | Loss 02.54 |
tensor(94.1814)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 2543.95 | Loss 02.94 |
tensor(104.7360)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 2531.89 | Loss 03.27 |
tensor(55.6342)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 1775.89 | Loss 01.74 |
tensor(76.4718)
[Training]| Epochs   0 | Batch 531285 /   127 | ms/batch 2162.96 | Loss 02.39 |
tensor(56.0167)
[Training]| Epochs   0 

In [77]:
'''
def batchify(data, batch_size, is_reordered = False):
        num_batch = len(data) // batch_size
        for i in range(num_batch):
        #    print(data[i * batch_size : (i + 1) * batch_size])
            t = data[i * batch_size : (i + 1) * batch_size]

            yield t
        u = num_batch*batch_size
        if len(data) % batch_size != 0:
            t = data[u : ]
#             print(residual)
          #  print(baskets)
#             baskets, lens, uids = sort_batch_of_lists(baskets, lens, uids)
#             padded_baskets = pad_batch_of_lists(baskets, 4071)
#             padded_lens = pad_batch_of_lists_2(lens, 4071)
#             padded_uids = pad_batch_of_lists_2(uids, 4071)
            yield t
'''

'''
def train_dream(train_ub):
    dr_model.train()  # turn on training mode for dropout
    dr_hidden = dr_model.init_hidden(32)
    total_loss = 0
    start_time = time()
    num_batchs = ceil(len(train_ub) / dr_config.batch_size)
    a = 0
    for x in (batchify(train_ub, dr_config.batch_size)):
        a += 32
        if (len(x) != 32):
            break
#         print("BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB")
#         print(x,"OOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOO  \n")
        baskets = []
        lens = []
        for num in x:
            baskets.append(num[1])
            lens.append(num[2])
#         dr_hidden = repackage_hidden(dr_hidden)  # repackage hidden state for RNN
        dr_model.zero_grad()  # optim.zero_grad()
        dynamic_user, _ = dr_model(baskets,lens,  dr_hidden)
#         print(dynamic_user.size())
#         print("-----------------------------------------------------------------------------")
        loss = bpr_loss(baskets, dynamic_user, dr_model.encode.weight, dr_config)
#         print(loss)
        loss.backward()

        # Clip to avoid gradient exploding
        torch.nn.utils.clip_grad_norm(dr_model.parameters(), dr_config.clip)

        # Parameter updating
        # manual SGD
        # for p in dr_model.parameters(): # Update parameters by -lr*grad
        #    p.data.add_(- dr_config.learning_rate, p.grad.data)
        # adam
        grad_norm = get_grad_norm(dr_model)
        previous_params = deepcopy(list(dr_model.parameters()))
        optim.step()

        total_loss += loss.data
        params = deepcopy(list(dr_model.parameters()))
        delta = get_weight_update(previous_params, params)
        weight_update_ratio = get_ratio_update(delta, params)
        print(total_loss)
        # Logging
        if i % dr_config.log_interval == 0 and i > 0:
            elapsed = (time() - start_time) * 1000 / dr_config.log_interval
            cur_loss = total_loss.item()/ dr_config.log_interval / dr_config.batch_size  # turn tensor into float
            total_loss = 0
            start_time = time()
            print(
                '[Training]| Epochs {:3d} | Batch {:5d} / {:5d} | ms/batch {:02.2f} | Loss {:05.2f} |'.format(epoch, i,
                                                                                                              num_batchs,
                                                                                                              elapsed,
                                                                                                              cur_loss))
            writer.add_scalar('model/train_loss', cur_loss, epoch * num_batchs + i)
            writer.add_scalar('model/grad_norm', grad_norm, epoch * num_batchs + i)
            writer.add_scalar('model/weight_update_ratio', weight_update_ratio, epoch * num_batchs + i)
'''

'''

def evaluate_dream(test_ub):
    dr_model.eval()
    dr_hidden = dr_model.init_hidden(32)

    total_loss = 0
    start_time = time()
    num_batchs = ceil(len(test_ub) / dr_config.batch_size)
    a = 0
    for  x in (batchify(test_ub, dr_config.batch_size)):
        a += 32
        if (len(x) != 32):
            break;
#         print("BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB")
#         print(x,"OOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOO  \n")
        baskets = []
        lens = []
        for num in x:
            baskets.append(num[1])
            lens.append(num[2])
        dynamic_user, _ = dr_model(baskets, lens, dr_hidden)
        loss = bpr_loss(baskets, dynamic_user, dr_model.encode.weight, dr_config)
#         dr_hidden = repackage_hidden(dr_hidden)
        total_loss += loss.data

    # Logging
    elapsed = (time() - start_time) * 1000 / num_batchs
    total_loss = total_loss.item() / num_batchs / dr_config.batch_size
    writer.add_scalar('model/eval_loss', total_loss, (epoch + 1) * num_batchs)
    writer.add_scalar('model/eval_loss', total_loss, (epoch + 1) * num_batchs)
    print('[Evaluation]| Epochs {:3d} | Elapsed {:02.2f} | Loss {:05.2f} |'.format(epoch, elapsed, total_loss))

'''
def eval_batch(dr_model, eval_ub, batch_size, is_reordered = False):
    '''
        Using dr_model to predict (u,p) score in batch
        Parameters:
        - ub: users' baskets
        - up: users' history purchases
        - batch_size
    '''
    dictionary_user_basket = {}
    for num in eval_ub:
        if not (num[0] in dictionary_user_basket.keys()):
            dictionary_user_basket[num[0]] = []
        dictionary_user_basket[num[0]].append(num[1]);
        
    # turn on evaluation mode
    dr_model.eval()
    item_embedding = dr_model.encode.weight
    dr_hidden = dr_model.init_hidden(batch_size)

    id_u, item_u, score_u, dynam_u = [], [], [], []
    start_time = time()
    num_batchs = ceil(len(eval_ub) / batch_size)
    for  x in enumerate(batchify(eval_ub, batch_size)):
#         if is_reordered is True:
#             baskets, lens, uids, r_baskets, h_baskets = x
#         else:
        
        for x in (batchify(eval_ub, dr_config.batch_size)):
#             print(x)
            if (len(x) != 32):
                break
    #         print("BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB")
    #         print(x,"OOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOOO  \n")
            baskets = []
            lens = []
            uids = []
            for num in x:
                baskets.append(num[1])
                for aj in num[2]:
                    lens.append(aj)
                uids.append(num[0])
    #         dr_hidden = repackage_hidden(dr_hidden)  # repackage hidden state for RNN
            dr_model.zero_grad()  # optim.zero_grad()
            dynamic_user, _ = dr_model(baskets,lens,  dr_hidden)
#
        dynamic_user, _ = dr_model(baskets, lens, dr_hidden)
#         print(dynamic_user)
        for uid, l, du in zip(uids, lens, dynamic_user):
#             print(type(uid), type(l), type(du))
            du_latest =  du[len(du) - 1].unsqueeze(0)
            # calculating <u,p> score for all history <u,p> pair 
            
            history_item = []
            for num in dictionary_user_basket[uid]:
                for k in num:
                    for l in k:
                        history_item.append(l)
#             print(history_item)
            history_item = torch.LongTensor(history_item) 
#             score_up = torch.mm(du_latest, item_embedding[history_item].t()).cpu().data.numpy()[0]
            id_u.append(uid), dynam_u.append(du_latest.cpu().data.numpy()[0]), item_u.append(history_item.cpu().numpy())#,score_u.append(score_up)
        # Logging
        elapsed = time() - start_time; start_time = time()
        print('[Predicting]| Batch {:5d} / {:5d} | seconds/batch {:02.02f}'.format(i, num_batchs, elapsed))
#         print(id_u)
    return id_u, item_u,  dynam_u



if __name__ == '__main__':
#     bc = BasketConstructor(constants.RAW_DATA_DIR, constants.FEAT_DATA_DIR)
#     ub_basket = bc.get_baskets('prior', reconstruct = False)
#     ub = Dataset(ub_basket)
#     up = bc.get_users_products('prior')
    
#     dr_config = Config(constants.DREAM_CONFIG)
#     with open(dr_config.checkpoint_dir, 'rb') as f:
#         dr_model = torch.load(f)
    dr_model.eval()    
#     ub = Dataset(ub_basket.head(64))
    id_u, item_u, dynam_u = eval_batch(dr_model, data_2, 32)
    print(item_u)


[Predicting]| Batch 531285 /   127 | seconds/batch 4.08
[Predicting]| Batch 531285 /   127 | seconds/batch 4.16
[Predicting]| Batch 531285 /   127 | seconds/batch 4.68
[Predicting]| Batch 531285 /   127 | seconds/batch 4.64
[Predicting]| Batch 531285 /   127 | seconds/batch 4.50
[Predicting]| Batch 531285 /   127 | seconds/batch 4.36
[Predicting]| Batch 531285 /   127 | seconds/batch 4.28
[Predicting]| Batch 531285 /   127 | seconds/batch 4.66
[Predicting]| Batch 531285 /   127 | seconds/batch 4.72
[Predicting]| Batch 531285 /   127 | seconds/batch 4.73
[Predicting]| Batch 531285 /   127 | seconds/batch 4.13
[Predicting]| Batch 531285 /   127 | seconds/batch 4.12
[Predicting]| Batch 531285 /   127 | seconds/batch 4.22
[Predicting]| Batch 531285 /   127 | seconds/batch 4.20
[Predicting]| Batch 531285 /   127 | seconds/batch 4.23
[Predicting]| Batch 531285 /   127 | seconds/batch 4.44
[Predicting]| Batch 531285 /   127 | seconds/batch 5.41
[Predicting]| Batch 531285 /   127 | seconds/bat

In [78]:
print(len(item_u))


4064


In [81]:
print(len(list(dictionary_customers_baskets.values())))

4035


In [82]:
print(len(id_u))

4064


In [83]:
print(id_u)

[17595.0, 14528.0, 17432.0, 16337.0, 14098.0, 15551.0, 16347.0, 13721.0, 16322.0, 17403.0, 16914.0, 16602.0, 12544.0, 13914.0, 13467.0, 17221.0, 17078.0, 13447.0, 15010.0, 18022.0, 16318.0, 17274.0, 15597.0, 17233.0, 16887.0, 13938.0, 17084.0, 14882.0, 15017.0, 12882.0, 17387.0, 13727.0, 17595.0, 14528.0, 17432.0, 16337.0, 14098.0, 15551.0, 16347.0, 13721.0, 16322.0, 17403.0, 16914.0, 16602.0, 12544.0, 13914.0, 13467.0, 17221.0, 17078.0, 13447.0, 15010.0, 18022.0, 16318.0, 17274.0, 15597.0, 17233.0, 16887.0, 13938.0, 17084.0, 14882.0, 15017.0, 12882.0, 17387.0, 13727.0, 17595.0, 14528.0, 17432.0, 16337.0, 14098.0, 15551.0, 16347.0, 13721.0, 16322.0, 17403.0, 16914.0, 16602.0, 12544.0, 13914.0, 13467.0, 17221.0, 17078.0, 13447.0, 15010.0, 18022.0, 16318.0, 17274.0, 15597.0, 17233.0, 16887.0, 13938.0, 17084.0, 14882.0, 15017.0, 12882.0, 17387.0, 13727.0, 17595.0, 14528.0, 17432.0, 16337.0, 14098.0, 15551.0, 16347.0, 13721.0, 16322.0, 17403.0, 16914.0, 16602.0, 12544.0, 13914.0, 13467.0, 

In [84]:
print(item_u[0])

[3523 3518 3749 3746 1695 3444  202 1280  908 1833  833  667  834 3477
 3476  352 1338 1937 1564  557 3980 3639 3564 1280 3242 1613 1642 3088
 1370 1132 3452 3461 3492  666]


In [85]:
for i in range(len(id_u)):
    if (id_u[i] == 17595):
        print(item_u[i])

[3523 3518 3749 3746 1695 3444  202 1280  908 1833  833  667  834 3477
 3476  352 1338 1937 1564  557 3980 3639 3564 1280 3242 1613 1642 3088
 1370 1132 3452 3461 3492  666]
[3523 3518 3749 3746 1695 3444  202 1280  908 1833  833  667  834 3477
 3476  352 1338 1937 1564  557 3980 3639 3564 1280 3242 1613 1642 3088
 1370 1132 3452 3461 3492  666]
[3523 3518 3749 3746 1695 3444  202 1280  908 1833  833  667  834 3477
 3476  352 1338 1937 1564  557 3980 3639 3564 1280 3242 1613 1642 3088
 1370 1132 3452 3461 3492  666]
[3523 3518 3749 3746 1695 3444  202 1280  908 1833  833  667  834 3477
 3476  352 1338 1937 1564  557 3980 3639 3564 1280 3242 1613 1642 3088
 1370 1132 3452 3461 3492  666]
[3523 3518 3749 3746 1695 3444  202 1280  908 1833  833  667  834 3477
 3476  352 1338 1937 1564  557 3980 3639 3564 1280 3242 1613 1642 3088
 1370 1132 3452 3461 3492  666]
[3523 3518 3749 3746 1695 3444  202 1280  908 1833  833  667  834 3477
 3476  352 1338 1937 1564  557 3980 3639 3564 1280 3242 161

In [86]:
for num in item_u:
    print(len(num))

34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
25
37
7
90
6
20
5
20
14
34
18
15
10
21
29
52
28
28
33
38
29
19
16
79
30
28
38
20
90
19
27
22
2